# PSDSから取得したデータの解析

In [36]:
require "nyaplot"
require "nyaplot3d"
require "json"
require "daru"
require "statsample"

false

In [37]:
# センサー名一覧
sensor_names = {
  "32" => :ambient_temp,
  "96" => :systemboard_temp,
  "160" => :cpu1_temp,
  "224" => :cpu2_temp,
  "288" => :dimm_1a_temp,
  "1824" => :main_12v,
  "1888" => :main_5v,
  "1952" => :main_3_3v,
  "2272" => :cpu1_1_8v,
  "2336" => :cpu2_1_8v,
  "2400" => :fan1_sys,
  "2464" => :fan2_sys,
  "2528" => :fan3_sys,
  "2592" => :fan4_sys,
  "2656" => :fan5_sys,
  "3296" => :total_power
}

{"32"=>:ambient_temp, "96"=>:systemboard_temp, "160"=>:cpu1_temp, "224"=>:cpu2_temp, "288"=>:dimm_1a_temp, "1824"=>:main_12v, "1888"=>:main_5v, "1952"=>:main_3_3v, "2272"=>:cpu1_1_8v, "2336"=>:cpu2_1_8v, "2400"=>:fan1_sys, "2464"=>:fan2_sys, "2528"=>:fan3_sys, "2592"=>:fan4_sys, "2656"=>:fan5_sys, "3296"=>:total_power}

In [38]:
define_method :load_json do |file, value_column|
  response = JSON.load(File.read(file))
  data = response["result"]["data"][0]
  time_idx = data["columns"].index { |i| i["name"] == "time" }
  sensor_no_idx = data["columns"].index { |i| i["name"] == "sensor_no" }
  value_idx = data["columns"].index { |i| i["name"] == value_column }

  h = sensor_names.values.each_with_object({time: []}) {|name, h| h[name] = []}
  data["rows"].chunk_while { |i, j|
    i[time_idx] == j[time_idx]
  }.each do |rows|
    h[:time].push(rows[0][time_idx] / 1000.0 / 3600.0 / 24.0) # days since epoch
    rows.each { |row|
      no = row[sensor_no_idx]
      name = sensor_names[no]
      if name =~ /_temp\z/
        value = row[value_idx].to_f / 1000.0 - 273.15  # millikelvin to celsius
      else
        value = row[value_idx].to_f / 1000.0
      end
      h[name].push(value)
    }
  end
  return Daru::DataFrame.new(h, order: [:time] + sensor_names.values)
end
#df = load_json("6358153b-064b-5b11-bfc6-2a45cb0dc42a-30d30m.json", "mean")
df = load_json("24h.json", "value")

#<Daru::DataFrame:70335215430180 @name = 0c73f1cd-08d0-4006-a7aa-c25dddedfe9f @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        14 16848.6067       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...

In [39]:
df.describe

#<Daru::DataFrame:70335218371660 @name = 1cea265e-64af-43c8-9138-68436875c254 @size = 5>
           ambient_te  cpu1_1_8v  cpu1_temp  cpu2_1_8v  cpu2_temp dimm_1a_te   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys   main_12v  main_3_3v    main_5v systemboar       time total_powe 
     count       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523       3523 
      mean 19.1778313 1.78599205 33.2179960 1.77999999 33.6474595 22.3170593 6162.06642 6204.09877 5834.86801 6179.77859 6046.39227 11.9992506 3.39996026 5.12999999 23.4496168 16849.0991 93.9086006 
       std 3.85064500 0.00490129 4.94612023 3.06465052 4.71366809 4.04618582 175.905345 187.041898 172.580387 180.954177 154.250809 0.00666428 0.00062922 2.24741038 4.04523706 0.28959156 14.6672206 
       min       14.5       1.78       30.0       1.78       30.0       18.0     6000.0     6120.0     5760.0     6120.0     6000.0      11.94       3.39       5.13       19.0 16848.6031       92.0 
       max       27.5       1.79       71.0       1.78       66.0       35.0     7200.0     7200.0     6840.0     7200.0     6960.0       12.0        3.4       5.13       33.0 16849.6029      252.0

In [40]:
# 相関行列の計算
cm = Statsample::Bivariate.correlation_matrix(df)
open("correlation_matrix.csv", "w") do |f|
  columns = df.vectors.to_a.map(&:to_s)
  f.puts("," + columns.join(","))
  cm.rows.each_with_index do |row, i|
    f.puts(columns[i] + "," + row.join(","))
  end
end
cm

Matrix[[1.0, 0.253147757940157, 0.26623910716859633, 0.20356730089975586, 0.20171338890053075, 0.2564030534150739, -0.043242339717524524, -4.178154044552983e-11, 0.0036922158287337617, -0.1796295889936044, -4.17832883770632e-11, 0.11760820908592153, 0.1278003212599705, 0.12560745821434585, 0.12369943783739387, 0.0911754106153247, 0.02175640447380686], [0.253147757940157, 1.0, 0.9915773993378265, 0.8106607110555474, 0.8687829111250965, 0.9796280546445838, -0.1873241578306974, -1.7769736996934893e-14, -0.046300262525597546, -0.7175896418319389, -1.141109107679865e-14, 0.5923673592540472, 0.6463673089893872, 0.5908982122658389, 0.6138590564529625, 0.4943127946241528, 0.11693484295191174], [0.26623910716859633, 0.9915773993378265, 1.0, 0.8501569404994965, 0.8991062630207162, 0.9913344418029023, -0.2080396834754593, -1.0153051954832838e-15, -0.08444785483615151, -0.706733657055716, 9.317023999886345e-15, 0.5759548126344984, 0.6296150288658466, 0.5701659418199928, 0.5975962732326419, 0.47672

In [41]:
# CPU温度・システムボード温度・環境温度の時間推移をプロット

plot = Nyaplot::Plot.new
plot.add_with_df(df, :line, :time, :cpu1_temp).configure do |d|
  d.title("CPU1")
  d.color("#dd4444")
end
plot.add_with_df(df, :line, :time, :cpu2_temp).configure do |d|
  d.title("CPU2")
  d.color("#ddaa44")
end
plot.add_with_df(df, :line, :time, :systemboard_temp).configure do |d|
  d.title("Systemboard")
  d.color("#44bb44")
end
plot.add_with_df(df, :line, :time, :ambient_temp).configure do |d|
  d.title("Ambient")
end
plot.x_label("Time (days since epoch)")
plot.y_label("Temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007ff05e245148 @properties={:panes=>[#<Nyaplot::Plot:0x007ff05e247b50 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff05e247998 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_temp, :title=>"CPU1", :color=>"#dd4444"}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[30.0, 71.0]>, #<Nyaplot::Diagram:0x007ff05e246f70 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu2_temp, :title=>"CPU2", :color=>"#ddaa44"}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[30.0, 66.0]>, #<Nyaplot::Diagram:0x007ff05e246570 @properties={:type=>:line, :options=>{:x=>:time, :y=>:systemboard_temp, :title=>"Systemboard", :color=>"#44bb44"}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[19.0, 33.0]>, #<Nyaplot::Diagram:0x007ff05e245b20 @properties={:type=>:line, :options=>{:x=>:time, :y=>:ambient_temp, :title=>"Ambient"}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[14.5, 27.5]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"Temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[16848.603182453702, 16849.602980578704], :yrange=>[14.5, 71.0]}}>], :data=>{"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"=>
#<Daru::DataFrame:70335215430180 @name = 0c73f1cd-08d0-4006-a7aa-c25dddedfe9f @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       

## CPU温度と環境温度の相関を調べる

In [42]:
plot = Nyaplot::Plot.new
plot.add_with_df(df, :scatter, :cpu1_temp, :ambient_temp)
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007ff063b56840 @properties={:panes=>[#<Nyaplot::Plot:0x007ff063b57330 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff063b57178 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[30.0, 71.0], @yrange=[14.5, 27.5]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :zoom=>true, :width=>700, :xrange=>[30.0, 71.0], :yrange=>[14.5, 27.5]}}>], :data=>{"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"=>
#<Daru::DataFrame:70335215430180 @name = 0c73f1cd-08d0-4006-a7aa-c25dddedfe9f @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        14 16848.6067       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ..

In [43]:
# CPU温度の下限値を除外
filtered_df = df.where(df[:cpu1_temp].gt(30.0))
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_temp, :ambient_temp)
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007ff05dd36fa8 @properties={:panes=>[#<Nyaplot::Plot:0x007ff05dd37ac0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff05dd378e0 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp}, :data=>"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"}, @xrange=[31.0, 71.0], @yrange=[16.0, 27.5]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :zoom=>true, :width=>700, :xrange=>[31.0, 71.0], :yrange=>[16.0, 27.5]}}>], :data=>{"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"=>
#<Daru::DataFrame:70335141626000 @name = d86fb968-f2e5-46b8-afeb-28ef1f41b9fc @size = 1753>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        18 16848.6078       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        19 16848.6080       18.0       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        20 16848.6083       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        21 16848.6085       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        25 16848.6096       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
        26 16848.6098       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6120.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ..

In [44]:
# 単回帰分析
sr = Statsample::Regression.simple(filtered_df[:cpu1_temp], filtered_df[:ambient_temp])
cpu1_temp_min = filtered_df[:cpu1_temp].min
cpu1_temp_max = filtered_df[:cpu1_temp].max
df2 = Daru::DataFrame.new(
  cpu1_temp_min.step(cpu1_temp_max, (cpu1_temp_max - cpu1_temp_min) / 10.0).map { |x|
    { x: x, y: sr.a + sr.b * x }
  }
)
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_temp, :ambient_temp).configure do |d|
  d.title("Sample")
end
plot.add_with_df(df2, :line, :x, :y).configure do |d|
  d.color("#44bb44")
  d.title(format("%.3f + %.3fx", sr.a, sr.b))
end
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.legend(true)
plot.show


#<Nyaplot::Frame:0x007ff064400ea0 @properties={:panes=>[#<Nyaplot::Plot:0x007ff064402520 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff064402368 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp, :title=>"Sample"}, :data=>"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"}, @xrange=[31.0, 71.0], @yrange=[16.0, 27.5]>, #<Nyaplot::Diagram:0x007ff0644019e0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :color=>"#44bb44", :title=>"9.066 + 0.361x"}, :data=>"c16463fb-139d-4a83-b2e4-55d48b849f94"}, @xrange=[31.0, 71.0], @yrange=[20.243951704517052, 34.66737683799622]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[31.0, 71.0], :yrange=>[16.0, 34.66737683799622]}}>], :data=>{"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"=>
#<Daru::DataFrame:70335141626000 @name = d86fb968-f2e5-46b8-afeb-28ef1f41b9fc @size = 1753>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        18 16848.6078       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        19 16848.6080       18.0       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        20 16848.6083       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        21 16848.6085       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        25 16848.6096       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
        26 16848.6098       17.5       22.0       31.0       31.0       21.0       12.0      

In [45]:
filtered_df.where(filtered_df[:cpu1_temp].gt(31.0) & filtered_df[:ambient_temp].lt(16))

#<Daru::DataFrame:70335146257200 @name = 97e1e7f4-4de6-4c84-8126-fb51d0ea84ef @size = 0>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe

In [46]:
# マハラノビス距離の計算

covariance_matrix = Statsample::Bivariate.covariance_matrix(Daru::DataFrame.new(cpu1_temp: filtered_df[:cpu1_temp],
                                                                                ambient_temp: filtered_df[:ambient_temp]))
vi = covariance_matrix.inverse
delta = (filtered_df[:cpu1_temp] - filtered_df[:cpu1_temp].mean).zip(filtered_df[:ambient_temp] - filtered_df[:ambient_temp].mean)
mhalanobis_distance = delta.map { |a|
  v = Vector[*a]
  Math.sqrt((v.transpose * vi * v)[0])
}
df3 = Daru::DataFrame.new(time: filtered_df[:time], cpu1_temp: filtered_df[:cpu1_temp], ambient_temp: filtered_df[:ambient_temp],
  mhalanobis_distance: mhalanobis_distance)
df3.plot type: :line, x: :time, y: :mhalanobis_distance

#<Nyaplot::Frame:0x007ff05ac617c0 @properties={:panes=>[#<Nyaplot::Plot:0x007ff063c98190 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff05ac61e00 @properties={:type=>:line, :options=>{:x=>:time, :y=>:mhalanobis_distance}, :data=>"02bbe831-0faa-4734-9ed2-e54991aa5e1b"}, @xrange=[16848.603182453702, 16849.574155254628], @yrange=[0.15245913268136022, 13.847016986066032]>], :options=>{:zoom=>true, :width=>700, :xrange=>[16848.603182453702, 16849.574155254628], :yrange=>[0.15245913268136022, 13.847016986066032]}}>], :data=>{"02bbe831-0faa-4734-9ed2-e54991aa5e1b"=>#<Nyaplot::DataFrame:0x007ff05ab7e768 @name="02bbe831-0faa-4734-9ed2-e54991aa5e1b", @rows=[{:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.603182453702}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.603718055554}, {:ambient_temp=>18.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.7018849620361163, :time=>16848.604215925927}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.605244502312}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.605499016205}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.60574199074}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.60599770833}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.60625792824}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.606505300926}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.607827094907}, {:ambient_temp=>18.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.7018849620361163, :time=>16848.608068935184}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.60832269676}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.608573391204}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.609620532407}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.609877638886}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.61041951389}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.61118712963}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.611943622684}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.61376388889}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.615581631944}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.623101215275}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.625194965276}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.625989259257}, {:ambient_temp=>17.5, :cpu1_temp=>31.0, :mhalanobis_distance=>1.67874161695836, :time=>16848.62624797454}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.626510011574}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.62726921296}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.627539965277}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.62780290509}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.63192314815}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time=>16848.632189224536}, {:ambient_temp=>17.0, :cpu1_temp=>31.0, :mhalanobis_distance=>1.6645623483083334, :time

In [47]:
# マハラノビス距離が4より大きいデータを表示
df3.where(df3[:mhalanobis_distance].gt(4))

#<Daru::DataFrame:70335127483180 @name = b5bf5372-6c24-4d45-88e7-3f074c4bb90b @size = 43>
           ambient_te  cpu1_temp mhalanobis       time 
        52       17.0       47.0 5.15081424 16848.6753 
        53       17.0       54.0 7.91721325 16848.6756 
        54       17.0       58.0 9.50679715 16848.6759 
       394       21.5       53.0 6.72967365 16849.0504 
       395       21.0       59.0 9.21185212 16849.0507 
       396       21.0       62.0 10.4114383 16849.0510 
       397       21.0       65.0 11.6110923 16849.0513 
       398       21.0       66.0 12.0109885 16849.0516 
       399       21.5       68.0 12.7286092 16849.0519 
       400       21.5       69.0 13.1285589 16849.0521 
       401       21.5       69.0 13.1285589 16849.0524 
       402       21.5       70.0 13.5285099 16849.0527 
       403       22.0       70.0 13.4470472 16849.0530 
       404       22.0       71.0 13.8470169 16849.0533 
       405       22.0       71.0 13.8470169 16849.0536 
       ...        ...        ...        ...        ...

In [48]:
# マハラノビス距離が4より小さいデータのみで単回帰分析
df4 = df3.where(df3[:mhalanobis_distance].lt(4))
sr = Statsample::Regression.simple(df4[:cpu1_temp], df4[:ambient_temp])
cpu1_temp_min = df4[:cpu1_temp].min
cpu1_temp_max = df4[:cpu1_temp].max
df5 = Daru::DataFrame.new(
  cpu1_temp_min.step(cpu1_temp_max, (cpu1_temp_max - cpu1_temp_min) / 10.0).map { |x|
    { x: x, y: sr.a + sr.b * x }
  }
)
plot = Nyaplot::Plot.new
plot.add_with_df(df4, :scatter, :cpu1_temp, :ambient_temp).configure do |d|
  d.title("Sample")
end
plot.add_with_df(df5, :line, :x, :y).configure do |d|
  d.color("#44bb44")
  d.title(format("%.3f + %.3fx", sr.a, sr.b))
end
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007ff063a02688 @properties={:panes=>[#<Nyaplot::Plot:0x007ff063a03d08 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff063a03b50 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp, :title=>"Sample"}, :data=>"4affc34b-aacc-438b-8ca5-8207566c77ba"}, @xrange=[31.0, 46.0], @yrange=[16.0, 27.5]>, #<Nyaplot::Diagram:0x007ff063a031a0 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :color=>"#44bb44", :title=>"-9.758 + 0.891x"}, :data=>"f551c21d-b52b-4b17-b718-134a20be3cd4"}, @xrange=[31.0, 46.0], @yrange=[17.864462727198255, 31.230077923077502]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[31.0, 46.0], :yrange=>[16.0, 31.230077923077502]}}>], :data=>{"4affc34b-aacc-438b-8ca5-8207566c77ba"=>
#<Daru::DataFrame:70335221769660 @name = 4affc34b-aacc-438b-8ca5-8207566c77ba @size = 1710>
           ambient_te  cpu1_temp mhalanobis       time 
         0       17.5       31.0 1.67874161 16848.6031 
         1       17.5       31.0 1.67874161 16848.6037 
         2       18.0       31.0 1.70188496 16848.6042 
         3       17.5       31.0 1.67874161 16848.6052 
         4       17.5       31.0 1.67874161 16848.6054 
         5       17.5       31.0 1.67874161 16848.6057 
         6       17.5       31.0 1.67874161 16848.6059 
         7       17.5       31.0 1.67874161 16848.6062 
         8       17.5       31.0 1.67874161 16848.6065 
         9       17.5       31.0 1.67874161 16848.6078 
        10       18.0       31.0 1.70188496 16848.6080 
        11       17.5       31.0 1.67874161 16848.6083 
        12       17.5       31.0 1.67874161 16848.6085 
        13       17.5       31.0 1.67874161 16848.6096 
        14       17.5       31.0 1.67874161 16848.6098 
       ...        ...        ...        ...        ... 
, "f551c21d-b52b-4b17-b718-134a20be3cd4"=>
#<Daru::DataFrame:70335220338100 @name = f551c21d-b52b-4b17-b718-134a20be3cd4 @size = 11>
                    x          y 
         0       31.0 17.8644627 
         1       32.5 19.2010242 
         2       34.0 20.5375857 
         3       35.5 21.8741472 
         4       37.0 23.2107088 
         5       38.5 24.5472703 
         6       40.0 25.8838318 
         7       41.5 27.2203933 
         8       43.0 28.5569548 
         9       44.5 29.8935164 
        10       46.0 31.2300779 
}, :extension=>["Elegans"]}>

In [49]:
plot = Nyaplot::Plot.new
plot.add_with_df(df, :line, :time, :cpu1_1_8v)
plot.x_label("Time (days since epoch)")
plot.y_label("CPU1 Voltage (W)")
plot.show

#<Nyaplot::Frame:0x007ff05dd43320 @properties={:panes=>[#<Nyaplot::Plot:0x007ff05dd43e10 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff05dd43c58 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_1_8v}, :data=>"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[1.78, 1.79]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"CPU1 Voltage (W)", :zoom=>true, :width=>700, :xrange=>[16848.603182453702, 16849.602980578704], :yrange=>[1.78, 1.79]}}>], :data=>{"0c73f1cd-08d0-4006-a7aa-c25dddedfe9f"=>
#<Daru::DataFrame:70335215430180 @name = 0c73f1cd-08d0-4006-a7aa-c25dddedfe9f @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        14 16848.6067       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...  

In [50]:
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_1_8v, :cpu1_temp)
plot.x_label("CPU1 Voltage (V)")
plot.y_label("CPU1 temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007ff05b518558 @properties={:panes=>[#<Nyaplot::Plot:0x007ff05b519098 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff05b518ee0 @properties={:type=>:scatter, :options=>{:x=>:cpu1_1_8v, :y=>:cpu1_temp}, :data=>"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"}, @xrange=[1.78, 1.79], @yrange=[31.0, 71.0]>], :options=>{:x_label=>"CPU1 Voltage (V)", :y_label=>"CPU1 temperature (℃)", :zoom=>true, :width=>700, :xrange=>[1.78, 1.79], :yrange=>[31.0, 71.0]}}>], :data=>{"d86fb968-f2e5-46b8-afeb-28ef1f41b9fc"=>
#<Daru::DataFrame:70335141626000 @name = d86fb968-f2e5-46b8-afeb-28ef1f41b9fc @size = 1753>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        18 16848.6078       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        19 16848.6080       18.0       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        20 16848.6083       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        21 16848.6085       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        25 16848.6096       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
        26 16848.6098       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6120.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ... 
}, :ext

In [51]:
df5 = load_json("24h.json", "value")
df6 = df5.where(df5[:time].gteq(16849.0) & df5[:time].lteq(16849.4))

#<Daru::DataFrame:70335191673660 @name = a5ed478d-ef3a-4fa4-a368-e3c723b679a8 @size = 1418>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
      1410 16849.0000       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1411 16849.0003       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1412 16849.0006       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1413 16849.0008       18.5       22.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
      1414 16849.0012       18.5       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1415 16849.0014       18.5       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1416 16849.0017       18.0       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
      1417 16849.0020       18.5       23.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1418 16849.0023       18.5       23.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
      1419 16849.0026       18.5       22.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1420 16849.0029       18.0       23.0       32.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1421 16849.0031       18.0       23.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1422 16849.0034       18.5       23.0       32.0       33.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1423 16849.0037       18.5       23.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
      1424 16849.0040       18.5       23.0       32.0       33.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...

In [52]:
# 昨日のCPU温度・システムボード温度・環境温度の時間推移をプロット

plot = Nyaplot::Plot.new
plot.add_with_df(df6, :line, :time, :cpu1_temp).configure do |d|
  d.title("CPU1")
  d.color("#dd4444")
end
plot.add_with_df(df6, :line, :time, :cpu2_temp).configure do |d|
  d.title("CPU2")
  d.color("#ddaa44")
end
plot.add_with_df(df6, :line, :time, :systemboard_temp).configure do |d|
  d.title("Systemboard")
  d.color("#44bb44")
end
plot.add_with_df(df6, :line, :time, :ambient_temp).configure do |d|
  d.title("Ambient")
end
plot.x_label("Time (days since epoch)")
plot.y_label("Temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007ff05dce6710 @properties={:panes=>[#<Nyaplot::Plot:0x007ff0598790f0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007ff059878f38 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_temp, :title=>"CPU1", :color=>"#dd4444"}, :data=>"a5ed478d-ef3a-4fa4-a368-e3c723b679a8"}, @xrange=[16849.00004435185, 16849.399972060186], @yrange=[31.0, 71.0]>, #<Nyaplot::Diagram:0x007ff059878510 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu2_temp, :title=>"CPU2", :color=>"#ddaa44"}, :data=>"a5ed478d-ef3a-4fa4-a368-e3c723b679a8"}, @xrange=[16849.00004435185, 16849.399972060186], @yrange=[31.0, 66.0]>, #<Nyaplot::Diagram:0x007ff05dce7ae8 @properties={:type=>:line, :options=>{:x=>:time, :y=>:systemboard_temp, :title=>"Systemboard", :color=>"#44bb44"}, :data=>"a5ed478d-ef3a-4fa4-a368-e3c723b679a8"}, @xrange=[16849.00004435185, 16849.399972060186], @yrange=[22.0, 33.0]>, #<Nyaplot::Diagram:0x007ff05dce70e8 @properties={:type=>:line, :options=>{:x=>:time, :y=>:ambient_temp, :title=>"Ambient"}, :data=>"a5ed478d-ef3a-4fa4-a368-e3c723b679a8"}, @xrange=[16849.00004435185, 16849.399972060186], @yrange=[18.0, 27.5]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"Temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[16849.00004435185, 16849.399972060186], :yrange=>[18.0, 71.0]}}>], :data=>{"a5ed478d-ef3a-4fa4-a368-e3c723b679a8"=>
#<Daru::DataFrame:70335191673660 @name = a5ed478d-ef3a-4fa4-a368-e3c723b679a8 @size = 1418>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
      1410 16849.0000       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1411 16849.0003       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1412 16849.0006       18.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1413 16849.0008       18.5       22.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
      1414 16849.0012       18.5       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1415 16849.0014       18.5       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1416 16849.0017       18.0       22.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6120.0       92.0 
      1417 16849.0020       18.5       23.0       31.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1418 16849.0023       18.5       23.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
      1419 16849.0026       18.5       22.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1420 16849.0029       18.0       23.0       32.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
      1421 16849.0031       18.0       23.0       32.0       33.0       21.0       12.0       5.13        3.4       1.79       1.78 